In [9]:
import pandas as pd
import seaborn as sb
import matplotlib.pyplot as plt
import numpy as np
%matplotlib inline
from sklearn import preprocessing
from itertools import islice
import seaborn as sns
from sklearn.cluster import KMeans

In [10]:
import warnings
warnings.filterwarnings('ignore')

In [12]:
dataFrame = pd.read_csv("../data/Week1_challenge.csv", na_values=['?', None])
#rename columns
dataFrame=dataFrame.rename(columns = {'Total DL (Bytes)' : 'totalDL','Total UL (Bytes)' : 'totalUL','Dur. (ms)' : 
                                      'dur','MSISDN/Number':'msisdn','Last Location Name':'location',
                                      'Handset Manufacturer':'manufacturer','Handset Type':'handset'
                                     })

### The following 5 cells are concerned with clustering users based on the engagement metrics.

In [13]:
sessionsCountData=dataFrame['msisdn'].value_counts()
sessionsCount=sessionsCountData.values.tolist()
msisdn=sessionsCountData.index.values
sessionPerUserDictionary = dict(zip(msisdn, sessionsCount))

durationSumDF=dataFrame.groupby('msisdn')['dur'].sum()
duration = durationSumDF.values.tolist()
msisdn=durationSumDF.index.values
durationPerUser = dict(zip(msisdn, duration))

sum_column = dataFrame["totalUL"] + dataFrame["totalDL"]
dataFrame["totalData"] = sum_column
totalDataDF=dataFrame.groupby('msisdn')['totalData'].sum()
totalData = totalDataDF.values.tolist()
msisdn=totalDataDF.index.values

totalDataUserDictionary = dict(zip(msisdn, totalData))

In [14]:
userEngagementDF=pd.DataFrame(columns=['MSISDN' ,'Session Frequency','Session Duration','Total Data'])
userEngagementDF['MSISDN']=durationPerUser.keys()

userEngagementDF['Session Frequency']=userEngagementDF['MSISDN'].map(sessionPerUserDictionary)
userEngagementDF['Session Duration']=userEngagementDF['MSISDN'].map(durationPerUser)
userEngagementDF['Total Data']= userEngagementDF['MSISDN'].map(totalDataUserDictionary)


In [15]:
x = userEngagementDF[['Session Frequency','Session Duration','Total Data']].values.astype(float)
min_max_scaler = preprocessing.MinMaxScaler()
x_scaled = min_max_scaler.fit_transform(x)
normalized = pd.DataFrame(x_scaled,columns=['Session Frequency','Session Duration','Total Data'])

In [16]:
KMean_clust= KMeans(n_clusters=3, init='k-means++',max_iter=1000)
KMean_clust.fit(normalized)

KMeans(max_iter=1000, n_clusters=3)

In [17]:
normalized['Cluster']= KMean_clust.labels_
normalized['MSISDN']= durationPerUser.keys()
userEngagementDF['MSISDN']= durationPerUser.keys()
normalized.sample(10)

metricDF=userEngagementDF[['Session Frequency','Session Duration','Total Data']]
metricDF['Cluster']=KMean_clust.labels_

## Cluster 0 has the lowest mean in all of the metrics. So cluster 0 is the cluster with the lowest engagement.

In [18]:
clusteredMean = metricDF.groupby('Cluster').mean()
clusteredMean

Session Frequency  Session Duration    Total Data
Cluster                                                   
0                 1.042238     106985.013467  4.955072e+08
1                 4.248708     569517.630258  2.280905e+09
2                 2.176267     213616.483959  1.125494e+09

### The following cell determines the centroid of each cluster and use it the centroid of the less engaged cluster to calculate the score for each user.

In [19]:
centroids = KMean_clust.cluster_centers_
centroids = min_max_scaler.inverse_transform(centroids)
print(centroids)
userEngagementDF['Score'] = np.linalg.norm( userEngagementDF[['Session Frequency', 'Session Duration','Total Data']].sub(np.array(centroids[0])), axis=1)
userEngagementDF

[[1.04210825e+00 1.06976349e+05 4.95490323e+08]
 [4.24644084e+00 5.69173587e+05 2.27960985e+09]
 [2.17574189e+00 2.13511494e+05 1.12500080e+09]]


MSISDN  Session Frequency  Session Duration    Total Data  \
0       3.360100e+10                  1          116720.0  8.786906e+08   
1       3.360100e+10                  1          181230.0  1.568596e+08   
2       3.360100e+10                  1          134969.0  5.959665e+08   
3       3.360101e+10                  1           49878.0  4.223207e+08   
4       3.360101e+10                  2           37104.0  1.457411e+09   
...              ...                ...               ...           ...   
106851  3.379000e+10                  1            8810.0  7.146416e+08   
106852  3.379000e+10                  1          140988.0  4.803073e+08   
106853  3.197021e+12                  1          877385.0  2.321240e+08   
106854  3.370000e+14                  1          253030.0  5.962878e+08   
106855  8.823971e+14                  1          869844.0  1.391536e+08   

               Score  
0       3.832003e+08  
1       3.386307e+08  
2       1.004762e+08  
3       7.316965e+07  
4       9.619206e+08  
...              ...  
106851  2.191513e+08  
106852  1.518303e+07  
106853  2.633675e+08  
106854  1.007976e+08  
106855  3.563375e+08  

[106856 rows x 5 columns]

## The following cells cluster users based on the experience metrics.

In [20]:
dataFrame=dataFrame.rename(columns = {'Total DL (Bytes)' : 'totalDL','Total UL (Bytes)' : 'totalUL','Dur. (ms)' : 
                                      'dur','msisdn':'MSISDN','Last Location Name':'location',
                                      'Handset Manufacturer':'manufacturer','Handset Type':'handset',
                                      'Avg RTT DL (ms)':'AVG RTT DL',
                                      'Avg RTT UL (ms)':'AVG RTT UL',
                                      'Avg Bearer TP UL (kbps)':'AVG TP UL',
                                      'Avg Bearer TP DL (kbps)':'AVG TP DL',
                                      'TCP UL Retrans. Vol (Bytes)':'TCP UL Retrans',
                                      'TCP DL Retrans. Vol (Bytes)':'TCP DL Retrans'
                                      
                                     
                                     })
userExperienceDF=dataFrame[['AVG RTT DL','AVG RTT UL','TCP UL Retrans','TCP DL Retrans','AVG TP UL','AVG TP DL']]
sumNull = userExperienceDF.isnull().sum()

for column in userExperienceDF.columns:
    if(column=='handset'):
        userExperienceDF[column] = userExperienceDF[column].fillna( userExperienceDF[column].mode().values[0] )
        userExperienceDF[column] = userExperienceDF[column].replace(['undefined'],userExperienceDF[column].mode().values[0])
    else:
        userExperienceDF[column] = userExperienceDF[column].fillna( userExperienceDF[column].mean() )
columns=userExperienceDF.columns
i=1
for column in columns:
    if(column!='handset'):
        Q1=userExperienceDF[column].quantile(0.25)
        Q3=userExperienceDF[column].quantile(0.75)
        IQR=Q3-Q1
        Lower_Whisker = Q1-1.5*IQR
        Upper_Whisker = Q3+1.5*IQR
        #print(Lower_Whisker, Upper_Whisker)
        userExperienceDF.loc[userExperienceDF[column] > Upper_Whisker, column] = userExperienceDF[column].mean()
userExperienceDF['AVG TCP'] = userExperienceDF['TCP UL Retrans']+userExperienceDF['TCP DL Retrans']
userExperienceDF['AVG RTT'] = userExperienceDF['AVG RTT UL']+userExperienceDF['AVG RTT DL']
userExperienceDF['AVG TP'] = userExperienceDF['AVG TP UL']+userExperienceDF['AVG TP DL']

userExperienceDF['MSISDN'] = dataFrame['MSISDN']
userExperienceTotalDF=userExperienceDF[['MSISDN','AVG TCP','AVG RTT','AVG TP']]
experiencePerUserDF = userExperienceTotalDF.groupby('MSISDN').sum()

experiencePerUserDF

AVG TCP     AVG RTT        AVG TP
MSISDN                                              
3.360100e+10  2.156957e+07   46.000000     76.000000
3.360100e+10  2.156957e+07   31.000000     99.000000
3.360100e+10  2.156957e+07  127.458589     97.000000
3.360101e+10  7.607247e+05   84.000000    248.000000
3.360101e+10  3.094040e+07  119.000000  42205.428647
...                    ...         ...           ...
3.379000e+10  2.180450e+05   52.000000  10365.000000
3.379000e+10  2.156957e+07   40.000000    116.000000
3.197021e+12  2.156957e+07  127.458589      1.000000
3.370000e+14  2.156957e+07  127.458589     33.000000
8.823971e+14  2.156957e+07  127.458589      2.000000

[106856 rows x 3 columns]

In [21]:
x = experiencePerUserDF[['AVG TCP','AVG RTT','AVG TP']].values.astype(float)
min_max_scaler = preprocessing.MinMaxScaler()
x_scaled = min_max_scaler.fit_transform(x)
normalized = pd.DataFrame(x_scaled,columns=['AVG TCP','AVG RTT','AVG TP'])
KMean_clust= KMeans(n_clusters=3, init='k-means++',max_iter=1000)
KMean_clust.fit(normalized)
metricDF=experiencePerUserDF[['AVG TCP','AVG RTT','AVG TP']]
metricDF['Cluster']=KMean_clust.labels_
metricDF

AVG TCP     AVG RTT        AVG TP  Cluster
MSISDN                                                       
3.360100e+10  2.156957e+07   46.000000     76.000000        2
3.360100e+10  2.156957e+07   31.000000     99.000000        2
3.360100e+10  2.156957e+07  127.458589     97.000000        2
3.360101e+10  7.607247e+05   84.000000    248.000000        0
3.360101e+10  3.094040e+07  119.000000  42205.428647        0
...                    ...         ...           ...      ...
3.379000e+10  2.180450e+05   52.000000  10365.000000        0
3.379000e+10  2.156957e+07   40.000000    116.000000        2
3.197021e+12  2.156957e+07  127.458589      1.000000        2
3.370000e+14  2.156957e+07  127.458589     33.000000        2
8.823971e+14  2.156957e+07  127.458589      2.000000        2

[106856 rows x 4 columns]

### The following cell determines the mean of the experience metrics for each cluster.

In [22]:
clusteredMean = metricDF.groupby('Cluster').mean()
clusteredMean

AVG TCP     AVG RTT        AVG TP
Cluster                                        
0        5.370528e+06   99.618576  21392.037371
1        3.784658e+07  375.957731  84560.073131
2        2.644630e+07   95.514100   2490.355100

### The following cell calculates satisfaction for each user as the average of engagement and experience scores.

In [23]:
centroids = KMean_clust.cluster_centers_
centroids = min_max_scaler.inverse_transform(centroids)

satisfactionDF=experiencePerUserDF
satisfactionDF['Exp Score'] = np.linalg.norm( experiencePerUserDF[['AVG TCP','AVG RTT','AVG TP']].sub(np.array(centroids[0])), axis=1)

# retreive engagement scores
satisfactionDF['Eng Score']=userEngagementDF['Score'].values
col = satisfactionDF.loc[: , "Eng Score":"Exp Score"]
satisfactionDF['Satisfaction'] = experiencePerUserDF[["Eng Score","Exp Score"]].mean(axis=1)
satisfactionDF=satisfactionDF[["Eng Score","Exp Score",'Satisfaction']]
#experiencePerUserDF['Satisfaction']=(experiencePerUserDF['Eng Score'] + experiencePerUserDF['Exp Score'])/2

satisfactionDF.nlargest(10,'Satisfaction')


Eng Score     Exp Score  Satisfaction
MSISDN                                                
3.361489e+10  8.350742e+09  1.290491e+08  4.239896e+09
3.376054e+10  8.019289e+09  2.448380e+08  4.132063e+09
3.362578e+10  8.004152e+09  2.568142e+08  4.130483e+09
3.362632e+10  7.475682e+09  2.314813e+08  3.853582e+09
3.367588e+10  7.395622e+09  1.619845e+08  3.778803e+09
3.365973e+10  7.210374e+09  8.427880e+07  3.647326e+09
3.366646e+10  6.813012e+09  1.256290e+08  3.469321e+09
3.376041e+10  6.636882e+09  1.098342e+08  3.373358e+09
3.366471e+10  6.376529e+09  1.086416e+08  3.242585e+09
3.369879e+10  6.045411e+09  1.384218e+08  3.091916e+09

In [24]:
import numpy as np
from sklearn.linear_model import LinearRegression

x = satisfactionDF[['Eng Score','Exp Score']]
y = satisfactionDF['Satisfaction']
x, y = np.array(x), np.array(y)
model = LinearRegression().fit(x, y)
r_sq = model.score(x, y)
print('coefficient determination:', r_sq)
print('intercept:', model.intercept_)
print('slope:', model.coef_)
y_pred = model.predict(x)
print('predicted response:', y_pred, sep='\n')

coefficient determination: 1.0
intercept: 1.1920928955078125e-07
slope: [0.5 0.5]
predicted response:
[1.99700548e+08 1.77415767e+08 5.83385048e+07 ... 1.39784162e+08
 5.84992263e+07 1.86269170e+08]


### The following cell runs k-means based engagement and experience score to group users into 2 clusters.

In [25]:
x = satisfactionDF[['Eng Score','Exp Score']].values.astype(float)
min_max_scaler = preprocessing.MinMaxScaler()
x_scaled = min_max_scaler.fit_transform(x)
normalized = pd.DataFrame(x_scaled,columns=['Eng Score','Exp Score'])
KMean_clust= KMeans(n_clusters=2, init='k-means++',max_iter=1000)
KMean_clust.fit(normalized)
satisfactionDF['Cluster']=KMean_clust.labels_
satisfactionDF

Eng Score     Exp Score  Satisfaction  Cluster
MSISDN                                                         
3.360100e+10  3.832003e+08  1.620085e+07  1.997005e+08        0
3.360100e+10  3.386307e+08  1.620085e+07  1.774158e+08        0
3.360100e+10  1.004762e+08  1.620085e+07  5.833850e+07        0
3.360101e+10  7.316965e+07  4.608065e+06  3.888886e+07        0
3.360101e+10  9.619206e+08  2.557167e+07  4.937461e+08        1
...                    ...           ...           ...      ...
3.379000e+10  2.191513e+08  5.150708e+06  1.121510e+08        0
3.379000e+10  1.518303e+07  1.620085e+07  1.569194e+07        0
3.197021e+12  2.633675e+08  1.620085e+07  1.397842e+08        0
3.370000e+14  1.007976e+08  1.620085e+07  5.849923e+07        0
8.823971e+14  3.563375e+08  1.620085e+07  1.862692e+08        0

[106856 rows x 4 columns]

### The following cell aggregates the average engagement and experience score for each cluster.

In [26]:
satisfactionDF.groupby('Cluster')[['Eng Score','Exp Score']].mean()

Eng Score     Exp Score
Cluster                            
0        2.500713e+08  1.297705e+07
1        9.857235e+08  4.147196e+07

## The following cell exports the dataframe containing engagement score, experience score and satisfaction to SQL. 

In [27]:
import sqlite3
con = sqlite3.connect ('telecom.db')
#print('The python version is...',sqlite3.version)

cursor = con.cursor ()
try:
    cur.execute ('create table user_satisfaction_level (user_id, eng_score number, exp_score number, Satisfaction)')
except :
    print('Table exists.... continuing')

satisfactionDF=satisfactionDF.rename(columns={"Eng Score": "eng_score", "Exp Score": "exp_score"})
satisfactionDF['user_id']=satisfactionDF.index
satisfactionDF[['user_id','eng_score','exp_score','Satisfaction']].to_sql('user_satisfaction_level', con, if_exists='replace', index=False)

satisfactionDF

Table exists.... continuing


eng_score     exp_score  Satisfaction  Cluster       user_id
MSISDN                                                                       
3.360100e+10  3.832003e+08  1.620085e+07  1.997005e+08        0  3.360100e+10
3.360100e+10  3.386307e+08  1.620085e+07  1.774158e+08        0  3.360100e+10
3.360100e+10  1.004762e+08  1.620085e+07  5.833850e+07        0  3.360100e+10
3.360101e+10  7.316965e+07  4.608065e+06  3.888886e+07        0  3.360101e+10
3.360101e+10  9.619206e+08  2.557167e+07  4.937461e+08        1  3.360101e+10
...                    ...           ...           ...      ...           ...
3.379000e+10  2.191513e+08  5.150708e+06  1.121510e+08        0  3.379000e+10
3.379000e+10  1.518303e+07  1.620085e+07  1.569194e+07        0  3.379000e+10
3.197021e+12  2.633675e+08  1.620085e+07  1.397842e+08        0  3.197021e+12
3.370000e+14  1.007976e+08  1.620085e+07  5.849923e+07        0  3.370000e+14
8.823971e+14  3.563375e+08  1.620085e+07  1.862692e+08        0  8.823971e+14

[106856 rows x 5 columns]

In [28]:
cursor.execute("SELECT * FROM user_satisfaction_level")

rows = cursor.fetchall()
rows=rows[:-10]
for row in rows:
        print(row)

    
con.close ()

(33601001722.0, 383200251.28478, 16200845.521594709, 199700548.40318736)
(33601001754.0, 338630687.98012537, 16200845.491408568, 177415766.73576698)
(33601002511.0, 100476164.06027906, 16200845.493915694, 58338504.777097374)
(33601007832.0, 73169647.11760987, 4608065.269844659, 38888856.19372727)
(33601008617.0, 961920623.6986108, 25571671.972941756, 493746147.83577627)
(33601010682.0, 119726988.41191494, 16963255.523515698, 68345121.96771532)
(33601011634.0, 159232744.59672832, 16311077.178328013, 87771910.88752817)
(33601011959.0, 162829967.13930914, 4608848.787366343, 83719407.96333773)
(33601014694.0, 494642018.9053626, 37770410.386697374, 266206214.64602998)
(33601020306.0, 236973438.83526304, 15442481.448815634, 126207960.14203934)
(33601021045.0, 380514313.12909085, 16200845.520344308, 198357579.32471758)
(33601021217.0, 134602128.62170434, 9225903.812876271, 71914016.21729031)
(33601022743.0, 13071244.374203147, 16200845.530783845, 14636044.952493496)
(33601024291.0, 136578489.

(33603433188.0, 270789385.854919, 16200845.516389344, 143495115.6856542)
(33603433374.0, 557984824.5199052, 16657802.616757708, 287321313.5683315)
(33603433551.0, 753778299.4440168, 4035629.902969786, 378906964.6734933)
(33603433662.0, 278694952.5987569, 2121120.228983086, 140408036.41387)
(33603435791.0, 486825330.01229036, 37770410.38245483, 262297870.1973726)
(33603436713.0, 109242999.43661286, 16200845.52947074, 62721922.4830418)
(33603437761.0, 229982874.549553, 37012045.889971204, 133497460.2197621)
(33603438056.0, 436085941.67973405, 16208485.43311975, 226147213.5564269)
(33603439317.0, 356267305.61822444, 5171035.394965882, 180719170.50659516)
(33603441734.0, 20198238.210494447, 4188390.2680974836, 12193314.239295965)
(33603448151.0, 200470474.9267532, 16200845.482219335, 108335660.20448627)
(33603450677.0, 27676543.887706652, 16200845.53876372, 21938694.713235185)
(33603452493.0, 787584362.8256879, 37265620.84473683, 412424991.83521235)
(33603452974.0, 176930947.54561773, 1620

(33605139455.0, 184085796.81558973, 16200845.503243055, 100143321.15941639)
(33605146889.0, 310927330.6354519, 15442647.527790086, 163184989.081621)
(33605150205.0, 1066237271.8641492, 38947259.34522891, 552592265.6046891)
(33605161020.0, 133588214.25910938, 16200845.521659888, 74894529.89038463)
(33605161321.0, 50172549.22921351, 16200845.509691915, 33186697.369452715)
(33605163415.0, 44226206.50780957, 5088582.028578121, 24657394.26819385)
(33605167049.0, 174684183.06263876, 16200845.465015706, 95442514.26382723)
(33605171079.0, 75493121.87599513, 17641212.541197, 46567167.208596066)
(33605175672.0, 177675664.0453799, 5346711.2677084915, 91511187.6565442)
(33605176493.0, 13276050.621296786, 16200845.503284229, 14738448.062290508)
(33605177173.0, 115547677.00979878, 16200845.505790168, 65874261.25779448)
(33605177895.0, 138108908.77831557, 15448834.511618186, 76778871.64496689)
(33605185843.0, 15313879.963643273, 16200845.451889224, 15757362.70776625)
(33605195739.0, 997155640.8811487

(33607283902.0, 241290468.64525548, 4609076.6023044605, 122949772.62377997)
(33607286942.0, 626153716.8967495, 37770410.402133994, 331962063.6494417)
(33607287423.0, 309881772.3423256, 5261100.941202367, 157571436.641764)
(33607293215.0, 75439453.45458977, 15448669.41828598, 45444061.436437875)
(33607296984.0, 230787214.72247496, 16200845.484810248, 123494030.10364261)
(33607297023.0, 521387031.01510555, 37770410.39255456, 279578720.70383006)
(33607301919.0, 278342305.3106974, 16200845.46121593, 147271575.38595665)
(33607306890.0, 22941535.636330172, 16200845.507200744, 19571190.57176546)
(33607308755.0, 247836595.51247218, 16200845.601897024, 132018720.5571846)
(33607313165.0, 239237752.17673713, 16200845.525477026, 127719298.85110708)
(33607315196.0, 372096702.50763035, 9387894.371934999, 190742298.43978268)
(33607315737.0, 149054517.5890949, 4608299.400287991, 76831408.49469145)
(33607316230.0, 15335947.800731087, 16200845.601897024, 15768396.701314054)
(33607316397.0, 205753280.678

(33608559185.0, 480582561.1139543, 37784081.25494135, 259183321.18444782)
(33608560937.0, 15673100.118491122, 16200845.45989002, 15936972.789190572)
(33608563340.0, 352871347.84546524, 5224289.066587026, 179047818.45602614)
(33608563355.0, 54128155.20443738, 16200845.500605216, 35164500.3525213)
(33608568908.0, 95273160.93435621, 16200845.488658927, 55737003.21150757)
(33608570952.0, 344014294.654768, 16200845.601897024, 180107570.1283325)
(33608576665.0, 259743463.63853392, 4833895.525708555, 132288679.58212124)
(33608583929.0, 140067026.32596704, 16200845.491417162, 78133935.9086921)
(33608584874.0, 220318048.22209635, 16200845.458451692, 118259446.84027402)
(33608585733.0, 289039351.4406806, 16200845.563722586, 152620098.50220162)
(33608587498.0, 14575615.35304719, 16201522.568674073, 15388568.960860632)
(33608589700.0, 1303835851.228385, 39844150.846530125, 671840001.0374576)
(33608601054.0, 141716862.17977086, 16243381.944972463, 78980122.06237166)
(33608601139.0, 344880783.029115

...

(33771618414.0, 18407219.94403042, 16200845.53876372, 17304032.741397068)
(33771620677.0, 386379385.45817626, 16200845.494001456, 201290115.47608885)
(33771632529.0, 59810104.56625545, 16200845.505774014, 38005475.036014736)
(33771633761.0, 141263385.64428118, 16200845.467641743, 78732115.55596146)
(33771635955.0, 1059613500.2181599, 59339981.142228745, 559476740.6801944)
(33771639000.0, 290198402.3817292, 1554025.1050082778, 145876213.74336874)
(33771643360.0, 303818714.15097904, 3810083.1945739556, 153814398.6727765)
(33771647413.0, 253999092.78622586, 16200845.486014102, 135099969.13612)
(33771652654.0, 81053434.33387186, 16960582.57807915, 49007008.4559755)
(33771655019.0, 651124910.5530121, 59339981.112952895, 355232445.83298254)
(33771655741.0, 189082155.1205978, 16200845.53732169, 102641500.32895975)
(33771658411.0, 425685364.8223036, 16295910.64622342, 220990637.7342635)
(33771661452.0, 22933203.403338693, 16200845.5058365, 19567024.454587597)
(33771661602.0, 77352339.31603672,

(33781310158.0, 111470042.39433996, 16200845.483516183, 63835443.938928075)
(33781310171.0, 38984048.93856233, 16200845.503265312, 27592447.220913824)
(33781312562.0, 904612523.1275826, 37770408.80666121, 471191465.9671219)
(33781312797.0, 736175173.3303133, 17382626.618054878, 376778899.9741841)
(33781313681.0, 208475396.41831726, 16200845.501860993, 112338120.96008913)
(33781314979.0, 984970564.6256663, 38532639.58518427, 511751602.10542524)
(33781316195.0, 204547091.9010014, 4596813.664448034, 104571952.78272471)
(33781316567.0, 91961654.65952343, 16200845.463682713, 54081250.06160307)
(33781317050.0, 344475960.8955426, 15442759.063221525, 179959359.97938207)
(33781321915.0, 17262221.782321624, 292980.2425230004, 8777601.012422312)
(33781321921.0, 387018644.6220957, 59339981.13694049, 223179312.8795181)
(33781326855.0, 117803240.00363919, 16200845.420432948, 67002042.71203607)
(33781328601.0, 149095732.0626389, 16200845.458451692, 82648288.7605453)
(33781329961.0, 32409795.8041851, 

(33782160090.0, 664981258.0624753, 16220885.345787548, 340601071.7041314)
(33782162594.0, 355594365.83917135, 16200845.503222343, 185897605.67119685)
(33782164809.0, 29673776.4016859, 16200845.495312152, 22937310.948499028)
(33782166158.0, 372639140.1024478, 16200845.538743006, 194419992.8205954)
(33782167091.0, 203409323.7422915, 5338155.421580646, 104373739.58193608)
(33782167720.0, 1232988101.5240173, 38530101.5655392, 635759101.5447782)
(33782167831.0, 354012288.4880516, 16207051.38779075, 185109669.93792117)
(33782169352.0, 78904645.12222444, 5097916.159144759, 42001280.6406846)
(33782171014.0, 328351927.4874435, 16200845.48734489, 172276386.4873942)
(33782173319.0, 78027172.4409331, 16200845.53863942, 47114008.98978626)
(33782173342.0, 320709472.87061155, 16200845.505899567, 168455159.18825555)
(33782173932.0, 298009257.1652387, 16200845.513708897, 157105051.33947378)
(33782176396.0, 41895352.712199256, 16200845.461077113, 29048099.086638182)
(33782177465.0, 777804080.2448037, 17

(33783367474.0, 283408142.5545242, 20164750.390487228, 151786446.47250572)
(33783368536.0, 1686488.6195964334, 4559757.261879961, 3123122.9407381974)
(33783368863.0, 201433286.44168648, 3351515.4050893867, 102392400.92338793)
(33783370389.0, 815389108.5556341, 20389595.36034513, 417889351.95798963)
(33783371963.0, 497033577.1854497, 16285461.253009012, 256659519.21922937)
(33783372370.0, 168505799.48283407, 16200845.51638514, 92353322.4996096)
(33783373398.0, 36173343.06839505, 3727480.2399507803, 19950411.654172916)
(33783374183.0, 413356300.6394223, 4606400.04904093, 208981350.3442316)
(33783376370.0, 504023008.6891714, 16212465.484860167, 260117737.08701578)
(33783377814.0, 333491909.24387765, 16200845.40747706, 174846377.32567737)
(33783380656.0, 135367792.173954, 16200845.49798889, 75784318.83597144)
(33783380781.0, 190000872.43722928, 5338653.434129114, 97669762.9356792)
(33783381902.0, 372514180.7137392, 3955153.8373594517, 188234667.27554932)
(33783382418.0, 545894618.9235705, 

(33787371723.0, 384780026.7013279, 5112206.642186393, 194946116.67175716)
(33787386716.0, 273693474.2592686, 16200845.558396222, 144947159.9088324)
(33787398347.0, 196138533.3526736, 16200845.493915694, 106169689.42329465)
(33787398511.0, 438929148.2434913, 37770410.361230224, 238349779.30236077)
(33787399118.0, 365425582.4419409, 17605383.78746736, 191515483.11470413)
(33787399736.0, 364406110.94337195, 37770410.3813471, 201088260.66235954)
(33787401171.0, 297810976.56869656, 17249367.47792254, 157530172.02330956)
(33787403567.0, 2163394231.1611686, 80152294.40973432, 1121773262.7854514)
(33787404469.0, 391663212.252086, 16200845.50837689, 203932028.88023144)
(33787405820.0, 59248350.99696113, 16200845.53076769, 37724598.26386441)
(33787406295.0, 42588936.0826068, 5088150.848693769, 23838543.465650283)
(33787408224.0, 957995122.4362148, 16329400.889100417, 487162261.6626576)
(33787420990.0, 1073546758.1151805, 37770410.38220772, 555658584.2486941)
(33787425905.0, 599564546.2780339, 37